In [2]:
pip install librosa

   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   ---------------------------------------- 0.0/1.0 MB ? eta -:--:--
   -------------------------------

In [60]:
import os
import numpy as np
import pandas as pd
import librosa
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC
from sklearn.metrics import classification_report, confusion_matrix
import scipy.signal as signal

def load_sounds(dataset_path):
    metadata=pd.read_csv(os.path.join(dataset_path, 'metadata', 'UrbanSound8K.csv'))
    metadata=metadata[metadata['fold']== 1]
    return metadata

In [142]:
def apply_windows(audio_data, sr):
    """Apply different window functions to audio data."""
    windows = {
        'Rectangular': np.ones_like(audio_data),
        'Hann': np.hanning(len(audio_data)),
        'Hamming': signal.windows.hamming(len(audio_data))
    }
    
    windowed_data = {}
    spectrograms = {}
    spectrograms_on_normal = {}
    
    # Compute normal spectrogram
    stft_normal = librosa.stft(audio_data)
    spectrogram_normal = librosa.amplitude_to_db(np.abs(stft_normal))
    spectrograms_on_normal["Normal"] = spectrogram_normal
    
    for window_name, window in windows.items():
        # Apply window
        windowed_signal = audio_data * window
        
        # Compute STFT
        stft = librosa.stft(windowed_signal)
        spectrogram = librosa.amplitude_to_db(np.abs(stft))
        
        # Store results
        windowed_data[window_name] = windowed_signal
        spectrograms[window_name] = spectrogram
    
    return spectrograms, spectrograms_on_normal

In [161]:
metadata = load_sounds('UrbanSound8K\\UrbanSound8K\\')

window_features = {
    'Rectangular':[],
    'Hann':[],
    'Hamming':[]
}
processed_classes={}

for index, row in metadata.iterrows():
    class_name=row['class']
    
    # If this class hasn't been processed yet
    if class_name not in processed_classes:
        audio_path=os.path.join('UrbanSound8K\\UrbanSound8K\\', 'audio', f'fold{row["fold"]}', row['slice_file_name'])
        audio_data, sr=librosa.load(audio_path, duration=3)
        processed_classes[class_name]={
            'file_name': row['slice_file_name'],
            'audio_data': audio_data,
            'spectrograms': apply_windows(audio_data, sr)
        }
        
        if len(processed_classes) == 10:
            break




In [162]:
processed_classes

{'dog_bark': {'file_name': '101415-3-0-2.wav',
  'audio_data': array([-0.00011485, -0.00017083, -0.00017736, ..., -0.00911009,
         -0.00594216, -0.00585145], dtype=float32),
  'spectrograms': ({'Rectangular': array([[-29.83984 , -31.624586, -34.090366, ..., -34.090366, -23.953861,
            -14.433859],
           [-30.687927, -34.090366, -34.090366, ..., -34.090366, -21.829498,
            -14.160981],
           [-31.552069, -34.090366, -34.090366, ..., -34.090366, -20.98471 ,
            -13.188582],
           ...,
           [-34.090366, -34.090366, -34.090366, ..., -34.090366, -34.090366,
            -34.090366],
           [-34.090366, -34.090366, -34.090366, ..., -34.090366, -34.090366,
            -34.090366],
           [-34.090366, -34.090366, -34.090366, ..., -34.090366, -34.090366,
            -34.090366]], dtype=float32),
    'Hann': array([[-35.35748616, -35.35748616, -35.35748616, ..., -35.35748616,
            -35.35748616, -35.35748616],
           [-35.3574861

### Spectrogram of "Dog bark" audio without windowing

In [171]:
plt.figure(figsize=(12, 8))
librosa.display.specshow(processed_classes["dog_bark"]["spectrograms"][1]["Normal"], cmap="inferno",x_axis='time', y_axis='hz')
plt.colorbar(format="%+2.0f dB")
plt.title(f"{labels[0]} without windowing")
plt.xlabel("Time (s)")
plt.ylabel("Frequency (Hz)")
plt.tight_layout()
plt.savefig(f'Dog_bark_no_windowing_spectrogram.png')
plt.show()

### Spectrogram of rectangular windowing applied to "Dog bark" audio

In [172]:

plt.figure(figsize=(12, 8))
librosa.display.specshow(processed_classes["dog_bark"]["spectrograms"][0]["Rectangular"], cmap="inferno",x_axis='time', y_axis='hz')
plt.colorbar(format="%+2.0f dB")
plt.title(f"{labels[0]} with rectangular windowing")
plt.xlabel("Time (s)")
plt.ylabel("Frequency (Hz)")
plt.tight_layout()
plt.savefig(f'Dog_bark_with_rect_windowing_spectrogram.png')
plt.show()

### Spectrogram of Hann windowing applied to "Dog bark" audio

In [173]:
plt.figure(figsize=(12, 8))
librosa.display.specshow(processed_classes["dog_bark"]["spectrograms"][0]["Hann"], cmap="inferno",x_axis='time', y_axis='hz')
plt.colorbar(format="%+2.0f dB")
plt.title(f"{labels[0]} with Hann windowing")
plt.xlabel("Time (s)")
plt.ylabel("Frequency (Hz)")
plt.tight_layout()
plt.savefig(f'Dog_bark_with_Hann_windowing_spectrogram.png')
plt.show()

### Spectrogram of Hamming windowing applied to "Dog bark" audio

In [176]:
plt.figure(figsize=(12, 8))
librosa.display.specshow(processed_classes["dog_bark"]["spectrograms"][0]["Hamming"], cmap="inferno",x_axis='time', y_axis='hz')
plt.colorbar(format="%+2.0f dB")
plt.title(f"{labels[0]} with Hamming windowing")
plt.xlabel("Time (s)")
plt.ylabel("Frequency (Hz)")
plt.tight_layout()
plt.savefig(f'Dog_bark_with_Hamming_windowing_spectrogram.png')
plt.show()

### Spectrogram of "Gun shot" audio without windowing

In [179]:
plt.figure(figsize=(12, 8))
librosa.display.specshow(processed_classes["gun_shot"]["spectrograms"][1]["Normal"], cmap="inferno",x_axis='time', y_axis='hz')
plt.colorbar(format="%+2.0f dB")
plt.title(f"{labels[1]} without windowing")
plt.xlabel("Time (s)")
plt.ylabel("Frequency (Hz)")
plt.tight_layout()
plt.savefig(f'Gun_shot_without_windowing_spectrogram.png')
plt.show()

In [184]:
plt.figure(figsize=(20, 6))

classes = list(processed_classes.keys())

for i in range(10):
    plt.subplot(2, 5, i+1)
    spectrogram = processed_classes[classes[i]]['spectrograms'][1]['Normal']
    librosa.display.specshow(spectrogram, cmap='inferno', x_axis='time', y_axis='hz')
    plt.title(classes[i])
    plt.colorbar(format='%+2.0f dB')

plt.tight_layout()
plt.savefig('urban_sound_spectrograms.png')
plt.show()

In [188]:
plt.figure(figsize=(20, 6))

classes = list(processed_classes.keys())

for i in range(10):
    plt.subplot(2, 5, i+1)
    spectrogram = processed_classes[classes[i]]['spectrograms'][0]['Rectangular']
    librosa.display.specshow(spectrogram, cmap='inferno', x_axis='time', y_axis='hz')
    plt.title(classes[i])
    plt.colorbar(format='%+2.0f dB')

plt.tight_layout()
plt.savefig('urban_sound_spectrograms_Rectangular.png')
plt.show()

In [185]:
plt.figure(figsize=(20, 6))

classes = list(processed_classes.keys())

for i in range(10):
    plt.subplot(2, 5, i+1)
    spectrogram = processed_classes[classes[i]]['spectrograms'][0]['Hann']
    librosa.display.specshow(spectrogram, cmap='inferno', x_axis='time', y_axis='hz')
    plt.title(classes[i])
    plt.colorbar(format='%+2.0f dB')

plt.tight_layout()
plt.savefig('urban_sound_spectrograms_Hann.png')
plt.show()

In [187]:
plt.figure(figsize=(20, 6))

classes = list(processed_classes.keys())

for i in range(10):
    plt.subplot(2, 5, i+1)
    spectrogram = processed_classes[classes[i]]['spectrograms'][0]['Hamming']
    librosa.display.specshow(spectrogram, cmap='inferno', x_axis='time', y_axis='hz')
    plt.title(classes[i])
    plt.colorbar(format='%+2.0f dB')

plt.tight_layout()
plt.savefig('urban_sound_spectrograms_Hamming.png')
plt.show()

## Training classifiers

In [202]:
def calculate_snr(signal, noise):
    signal_power= np.mean(signal**2)
    noise_power= np.mean(noise**2)
    noise_power+=1e-4
    snr= 10*np.log10(signal_power / noise_power)
    return snr

def load_urbansound_dataset(dataset_path):
    metadata = pd.read_csv(os.path.join(dataset_path, 'metadata', 'UrbanSound8K.csv'))
    metadata=metadata[metadata['fold']== 1]
    return metadata

In [203]:
def apply_windows(audio_data):

    def rectangular_window(length):
        window = [1.0] * length
        return window
    
    windows = {
        'Rectangular': rectangular_window(len(audio_data)),
        'Hann': np.hanning(len(audio_data)),
        'Hamming': np.hamming(len(audio_data))
    }
    
    windowed_results = {}
    
    for window_name, window in windows.items():
        windowed_signal= audio_data*window
        
        # Compute noise (difference between original and windowed)
        noise=audio_data- windowed_signal
        
        # Calculate SNR
        snr= calculate_snr(audio_data, noise)
        
        stft=librosa.stft(windowed_signal)
        spectrogram= librosa.amplitude_to_db(np.abs(stft))
        
        windowed_results[window_name]={
            'signal': windowed_signal,
            'spectrogram': spectrogram,
            'snr': snr,
            'window': window}
    
    return windowed_results

In [204]:
def extract_features(spectrogram):
    """Extract mean and standard deviation features from spectrogram."""
    return np.concatenate([
        np.mean(spectrogram, axis=1),
        np.std(spectrogram, axis=1)
    ])

In [205]:
dataset_path='UrbanSound8K\\UrbanSound8K\\'
metadata = pd.read_csv(os.path.join(dataset_path, 'metadata', 'UrbanSound8K.csv'))
metadata=metadata[metadata['fold']== 1]
# Prepare feature matrices and result tracking
window_features = {'Rectangular': [], 'Hann': [], 'Hamming': []}
labels= []
snr_results= {}
spectrograms_by_class= {}

# Process each unique class
for class_name in metadata['class'].unique():
    class_samples = metadata[metadata['class'] == class_name]
    class_spectrograms = {}
    
    # Collect samples for this class
    for _, row in class_samples.iterrows():
        audio_path = os.path.join(dataset_path, 'audio', f'fold{row["fold"]}', row['slice_file_name'])
        
        # Load audio
        audio_data, _ = librosa.load(audio_path, duration=3)
        
        # Apply windows
        windowed_results = apply_windows(audio_data)
        
        # Store spectrograms for visualization
        class_spectrograms[row['slice_file_name']] = {
            name: result['spectrogram'] for name, result in windowed_results.items()
        }
        
        # Collect SNR results
        for window_name, result in windowed_results.items():
            if window_name not in snr_results:
                snr_results[window_name] = []
            snr_results[window_name].append(result['snr'])
            
            # Extract features
            features = extract_features(result['spectrogram'])
            window_features[window_name].append(features)
        
        labels.append(class_name)
    

# Print SNR statistics
print("SNR Statistics by Window Type:")
for window_name, snrs in snr_results.items():
    print(f"{window_name}: Mean SNR = {np.mean(snrs):.2f}, Std = {np.std(snrs):.2f}")

results={}
for window_name, features in window_features.items():
    X = np.array(features)
    X_train, X_test, y_train, y_test = train_test_split(X, labels, test_size=0.2, random_state=42)
    
    # Scale features
    scaler = StandardScaler()
    X_train_scaled = scaler.fit_transform(X_train)
    X_test_scaled = scaler.transform(X_test)
    
    # Train SVM
    svm = SVC(kernel='rbf')
    svm.fit(X_train_scaled, y_train)
    
    # Predict and evaluate
    y_pred = svm.predict(X_test_scaled)
    
    # Compute confusion matrix
    cm = confusion_matrix(y_test, y_pred)
    
    # Plot confusion matrix
    plt.figure(figsize=(10, 8))
    sns.heatmap(cm, annot=True, fmt='d', cmap='Blues', 
                xticklabels=sorted(set(labels)), 
                yticklabels=sorted(set(labels)))
    plt.title(f'Confusion Matrix - {window_name} Window')
    plt.xlabel('Predicted Label')
    plt.ylabel('True Label')
    plt.tight_layout()
    plt.savefig(f'{window_name}_confusion_matrix.png')
    plt.close()
    
    results[window_name] = {
        'classification_report': classification_report(y_test, y_pred),
        'confusion_matrix': cm
    }
    
    print(f"\n{window_name} Window Results:")
    print(results[window_name]['classification_report'])


C:\Users\Neermita Bhattachary\AppData\Local\Programs\Python\Python312\Lib\site-packages\librosa\core\spectrum.py:266: UserWarning: n_fft=2048 is too large for input signal of length=1103
  warnings.warn(
C:\Users\Neermita Bhattachary\AppData\Local\Programs\Python\Python312\Lib\site-packages\librosa\core\spectrum.py:266: UserWarning: n_fft=2048 is too large for input signal of length=1323
  warnings.warn(
C:\Users\Neermita Bhattachary\AppData\Local\Programs\Python\Python312\Lib\site-packages\librosa\core\spectrum.py:266: UserWarning: n_fft=2048 is too large for input signal of length=1523
  warnings.warn(


SNR Statistics by Window Type:
Rectangular: Mean SNR = 13.65, Std = 9.92
Hann: Mean SNR = 2.45, Std = 4.57
Hamming: Mean SNR = 3.02, Std = 4.73

Rectangular Window Results:
                  precision    recall  f1-score   support

 air_conditioner       0.85      0.94      0.89        18
        car_horn       1.00      0.57      0.73         7
children_playing       0.75      0.71      0.73        17
        dog_bark       0.88      0.81      0.85        27
        drilling       0.83      0.91      0.87        22
   engine_idling       0.82      0.78      0.80        23
        gun_shot       1.00      0.75      0.86         4
      jackhammer       0.74      1.00      0.85        20
           siren       0.87      0.72      0.79        18
    street_music       0.89      0.89      0.89        19

        accuracy                           0.83       175
       macro avg       0.86      0.81      0.83       175
    weighted avg       0.84      0.83      0.83       175


Hann Window

In [207]:
 results["Hann"]["confusion_matrix"]

array([[17,  0,  1,  0,  0,  0,  0,  0,  0,  0],
       [ 0,  6,  1,  0,  0,  0,  0,  0,  0,  0],
       [ 0,  0,  8,  0,  0,  0,  0,  2,  3,  4],
       [ 0,  0,  4, 20,  0,  1,  0,  1,  1,  0],
       [ 0,  0,  1,  0, 17,  0,  0,  0,  0,  4],
       [ 1,  0,  0,  0,  0, 19,  0,  2,  0,  1],
       [ 0,  0,  0,  1,  0,  0,  3,  0,  0,  0],
       [ 0,  0,  0,  0,  0,  0,  0, 20,  0,  0],
       [ 0,  0,  1,  0,  0,  4,  0,  1, 12,  0],
       [ 1,  0,  0,  1,  0,  0,  0,  2,  0, 15]], dtype=int64)